# Folium
***
<img src="data/ttiot.png" />

In [1]:
# !pip3 install folium
# https://python-visualization.github.io/folium/

In [2]:
from folium import Map, Marker, Icon, FeatureGroup, LayerControl, Choropleth
from folium.plugins import HeatMap
import pandas as pd

## Map

In [3]:
m = Map(location=[37.0902,-95.7129],zoom_start=4)
m

## Markers

In [4]:
capitals = pd.read_csv("data/us_capitals.csv",index_col=0)
capitals.head()

abbrev       state      capital   latitude   longitude  population
id                                                                   
1      AL     Alabama   Montgomery  32.380120  -86.300629      205764
2      AK      Alaska       Juneau  58.299740 -134.406794       31275
4      AZ     Arizona      Phoenix  33.448260 -112.075774     1445632
5      AR    Arkansas  Little Rock  34.748655  -92.274494      193524
6      CA  California   Sacramento  38.579065 -121.491014      466488

In [5]:
# https://getbootstrap.com/docs/3.3/components/
# https://fontawesome.com/v4.7.0/icons/
m = Map(location=[37.0902,-95.7129],zoom_start=4)
for i, row in capitals.iterrows():
    if row["population"] > 2e5: 
        icon = Icon(
                color="red",
                prefix="fa",
                icon="trophy"
            )
    else:
        icon = Icon(
                color="green",
                prefix="fa",
                icon="paw"
            )
    Marker(
        location=row[["latitude","longitude"]],
        tooltip=row["state"],
        popup=row["capital"],
        icon=icon
    ).add_to(m)
m

## HeatMap

In [6]:
df = pd.read_csv("data/ufo.csv")
df = df[df.country == "us"]
df.head()

datetime        city state country     shape  seconds    duration  \
0  10/10/1949 20:30  san marcos    tx      us  cylinder     2700  45 minutes   
3  10/10/1956 21:00        edna    tx      us    circle       20    1/2 hour   
4  10/10/1960 20:00     kaneohe    hi      us     light      900  15 minutes   
5  10/10/1961 19:00     bristol    tn      us    sphere      300   5 minutes   
7  10/10/1965 23:45     norwalk    ct      us      disk     1200  20 minutes   

                                            comments report_date   latitude  \
0  This event took place in early fall around 194...   4/27/2004  29.883056   
3  My older brother and twin sister were leaving ...   1/17/2004  28.978333   
4  AS a Marine 1st Lt. flying an FJ4B fighter/att...   1/22/2004  21.418056   
5  My father is now 89 my brother 52 the girl wit...   4/27/2007  36.595000   
7  A bright orange color changing to reddish colo...   10/2/1999  41.117500   

    longitude  
0  -97.941111  
3  -96.645833  
4 -157.803611  
5  -82.188889  
7  -73.408333

In [7]:
df.shape

(65114, 11)

In [8]:
m_heat = Map(location=[37.0902,-95.7129],zoom_start=4)
HeatMap(
    data=df[["latitude", "longitude"]],
    radius=13
).add_to(m_heat)
m_heat

In [9]:
df["category"] = pd.qcut(df.seconds,q=[0,0.25,0.5,1],labels=["short", "medium", "long"])
df.head()

datetime        city state country     shape  seconds    duration  \
0  10/10/1949 20:30  san marcos    tx      us  cylinder     2700  45 minutes   
3  10/10/1956 21:00        edna    tx      us    circle       20    1/2 hour   
4  10/10/1960 20:00     kaneohe    hi      us     light      900  15 minutes   
5  10/10/1961 19:00     bristol    tn      us    sphere      300   5 minutes   
7  10/10/1965 23:45     norwalk    ct      us      disk     1200  20 minutes   

                                            comments report_date   latitude  \
0  This event took place in early fall around 194...   4/27/2004  29.883056   
3  My older brother and twin sister were leaving ...   1/17/2004  28.978333   
4  AS a Marine 1st Lt. flying an FJ4B fighter/att...   1/22/2004  21.418056   
5  My father is now 89 my brother 52 the girl wit...   4/27/2007  36.595000   
7  A bright orange color changing to reddish colo...   10/2/1999  41.117500   

    longitude category  
0  -97.941111     long  
3  -96.645833    short  
4 -157.803611     long  
5  -82.188889     long  
7  -73.408333     long

## FeatureGroup & LayerControl

In [10]:
m_heat_cat = Map([37.0902,-95.7129], zoom_start=4)
for cat in df.category.unique():
    data = df[df.category==cat]
    group = FeatureGroup(
                name=f"{cat.title()} encounter",
                show=False
            )
    HeatMap(data=data[["latitude","longitude"]],radius = 13).add_to(group)
    group.add_to(m_heat_cat)
LayerControl(collapsed=False).add_to(m_heat_cat)
m_heat_cat

In [11]:
m_heat_shape = Map([37.0902,-95.7129], zoom_start=4)
for cat in df["shape"].unique():
    data = df[df["shape"]==cat]
    group = FeatureGroup(
                name=f"{cat} shaped",
                show=False
            )
    HeatMap(data=data[["latitude","longitude"]],radius = 13).add_to(group)
    group.add_to(m_heat_shape)
LayerControl(collapsed=False).add_to(m_heat_shape)
m_heat_shape

## Choropleth

In [12]:
state_data = df.groupby("state").agg(count=("state","count")).reset_index(level=0)
state_data.state = state_data.state.apply(lambda x: x.upper())

In [13]:
m_choro = Map([37.0902,-95.7129], zoom_start=4)

Choropleth(
    geo_data="data/us_states.json",
    name="number of sighting",
    data=state_data,
    columns=["state","count"],
    key_on="feature.id",
    fill_color='OrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='UFO Sightings'
).add_to(m_choro)
#LayerControl().add_to(m_choro)

m_choro

In [14]:
m_choro.save("choropleth.html")